In [ ]:
"Digital Twins in Maritime Industry"




In [36]:
from utils.paper import df


In [6]:
# List all columns that start with 'labels_'
label_columns = [col for col in df.columns if col.startswith('labels_')]
print(sorted(label_columns))

['labels_1', 'labels_10', 'labels_11', 'labels_12', 'labels_13', 'labels_14', 'labels_15', 'labels_16', 'labels_17', 'labels_18', 'labels_19', 'labels_2', 'labels_20', 'labels_21', 'labels_22', 'labels_23', 'labels_24', 'labels_25', 'labels_3', 'labels_4', 'labels_5', 'labels_6', 'labels_7', 'labels_8', 'labels_9']


In [11]:
for i in range(1, 26):
    column = f"labels_{i}"
    # Get unique cluster labels in the current column
    unique_clusters = df[column].unique()
    
    # Create a dictionary to hold DataFrames for each cluster
    cluster_dfs = {}
    
    # Split the DataFrame into separate DataFrames for each cluster
    for cluster in unique_clusters:
        # Select only the 'title' and 'abstract' columns for each cluster and limit to first 5 entries
        cluster_dfs[cluster] = df[df[column] == cluster][['title', 'abstract']].head(5)
        
        # Optionally, print or process each cluster DataFrame
        print(f"Cluster {cluster} in {column}:")
        print(cluster_dfs[cluster])  # Display the first 5 rows of the cluster DataFrame

Cluster 0 in labels_1:
                                               title  \
0  Maritime Digital Twin architecture: A concept ...   
1  Real-time digital twin for ship operation in w...   
2  Real-time digital twin of research vessel for ...   
3  Digital Twin in the Maritime Domain: A Review ...   
4  From digital twin to maritime data space: Tran...   

                                            abstract  
0  Digital Twins (DTs) play an important role in ...  
1  This paper introduces a real-time digital twin...  
2  Real-time digital twins of ships in operation ...  
3  This paper highlights the development of Digit...  
4  The concept of the digital twin is gaining mom...  
Cluster 1 in labels_2:
                                               title  \
0  Maritime Digital Twin architecture: A concept ...   
1  Real-time digital twin for ship operation in w...   
2  Real-time digital twin of research vessel for ...   
3  Digital Twin in the Maritime Domain: A Review ...   
4  From

In [15]:
for i in range(1, 26):
    column = f"labels_{i}"
    # Get unique cluster labels in the current column
    unique_clusters = sorted(df[column].unique())
    
    print(f"{len(unique_clusters)} clusters:")
    print("========")
    
    # Split the DataFrame into separate DataFrames for each cluster
    for cluster in unique_clusters:
        # Select only the 'title' column for each cluster and limit to first 5 entries
        titles = df[df[column] == cluster]['title'].head(5).tolist()
        
        # Truncate each title to a maximum of 30 characters
        truncated_titles = [title[:30] for title in titles]
        
        # Print the cluster number and titles
        print(f"{cluster}. ---- {', '.join(truncated_titles)}")

1 clusters:
0. ---- Maritime Digital Twin architec, Real-time digital twin for shi, Real-time digital twin of rese, Digital Twin in the Maritime D, From digital twin to maritime 
2 clusters:
0. ---- A survey on industrial informa, Model-driven digital twin cons, 3D CAD data extraction and con, A Cloud-based Digital Twin Man, Significant applications of bi
1. ---- Maritime Digital Twin architec, Real-time digital twin for shi, Real-time digital twin of rese, Digital Twin in the Maritime D, From digital twin to maritime 
3 clusters:
0. ---- Data-driven ship digital twin , Rapid acquisition method for s, A digital twin approach for ma, Enabling digital twins in the , Acquisition method of evaluati
1. ---- Maritime Digital Twin architec, Real-time digital twin for shi, Real-time digital twin of rese, Digital Twin in the Maritime D, From digital twin to maritime 
2. ---- A survey on industrial informa, 3D CAD data extraction and con, A Cloud-based Digital Twin Man, Significant applications 

In [31]:
level_headlines

{1: ['Headline for labels[0]  len(labels) = 1)'],
 2: ['Headline for labels[0]  len(labels) = 2)',
  'Headline for labels[1]  len(labels) = 2)'],
 3: ['Headline for labels[0]  len(labels) = 3)',
  'Headline for labels[1]  len(labels) = 3)',
  'Headline for labels[2]  len(labels) = 3)'],
 4: ['Headline for labels[0]  len(labels) = 4)',
  'Headline for labels[1]  len(labels) = 4)',
  'Headline for labels[2]  len(labels) = 4)',
  'Headline for labels[3]  len(labels) = 4)'],
 5: ['Headline for labels[0]  len(labels) = 5)',
  'Headline for labels[1]  len(labels) = 5)',
  'Headline for labels[2]  len(labels) = 5)',
  'Headline for labels[3]  len(labels) = 5)',
  'Headline for labels[4]  len(labels) = 5)'],
 6: ['Headline for labels[0]  len(labels) = 6)',
  'Headline for labels[1]  len(labels) = 6)',
  'Headline for labels[2]  len(labels) = 6)',
  'Headline for labels[3]  len(labels) = 6)',
  'Headline for labels[4]  len(labels) = 6)',
  'Headline for labels[5]  len(labels) = 6)'],
 7: ['Head

In [35]:
from openai import AzureOpenAI
from dotenv import load_dotenv  # for loading environment variables from a .env file
import os
load_dotenv()  # load environment variables from .env file


client = AzureOpenAI(
                azure_endpoint=os.getenv("AZURE_API_BASE"),
                api_version=os.getenv("AZURE_API_VERSION"),
                api_key=os.getenv("AZURE_API_KEY")
        )



In [45]:
from fasthtml.common import *
import pandas as pd
import re, os
from openai import AzureOpenAI
from rerankers import Reranker

from scipy import spatial
from dotenv import load_dotenv  # for loading environment variables from a .env file
load_dotenv()  # load environment variables from .env file


client = AzureOpenAI(
                azure_endpoint=os.getenv("AZURE_API_BASE"),
                api_version=os.getenv("AZURE_API_VERSION"),
                api_key=os.getenv("AZURE_API_KEY")
        )


import numpy as np
from sklearn.metrics.pairwise import cosine_distances
import ast
from utils.decorators import timed, timing
from typing import List, Optional
import json


In [63]:

@timed
def get_category_from_embeddings(titles, cluster_amount=None, current_cluster_nr=None, level_headlines=None):
    # Filter df so that it only includes the ones where the title is in titles list
    filtered_df = df[df['title'].isin(titles)]

    

    # Ensure the embedding column is evaluated to a list
    filtered_df['embedding'] = filtered_df['embedding'].apply(ast.literal_eval)

    # Calculate the centroid of the embeddings
    centroid = np.mean(filtered_df['embedding'].tolist(), axis=0)
    print(filtered_df['embedding'].tolist())
    # Calculate the cosine distance between each embedding and the centroid
    filtered_df['distance_to_centroid'] = cosine_distances(filtered_df['embedding'].tolist(), [centroid]).flatten()

    # Sort the DataFrame by distance to the centroid
    sorted_df = filtered_df.sort_values(by='distance_to_centroid')

    top_papers = sorted_df[['title', 'abstract']].head(20).to_dict(orient='records')

    # Prepare the prompt for OpenAI GPT-4
    prompt = "Based on the following titles and abstracts (that are sorted by distance to the centroid of their text embeddings on text+abstract), what is the common topic?\n\n"
    extra_system_prompt = ""
    if level_headlines is not None and cluster_amount is not None  and current_cluster_nr is not None:
        extra_system_prompt = f"""We are now processing one cluster out of {cluster_amount},
        Our approach is to process all papers and start naming clusters starting from having only 1 cluster, and then we split the papers into
        2 clusters, and name them and continue until we ahve 25 clusters, We should take into consideration that we have already named parent clusters.
        We dont want to repeat text in names that are siblings,
        We are currently named these clusters {level_headlines} (we are currently working on the final layer, you can see which ones we have already named)

        Make names specific, and bear in mind that the user will see the oter clusters simoultaneously 
        when this data is used, so avoid adding words that will be repeated in all clusters. And be to the point with headline and description, avoid text like 'this cluster is about...'""" + prompt

    for paper in top_papers:
        title = paper['title']
        abstract = paper['abstract']
        prompt += f"Title: {title}\nAbstract: {abstract}\n\n"


    print(extra_system_prompt)

    # Call OpenAI GPT-4 to get the topic
    response = client.chat.completions.create(
        model="gpt-4o",
        max_tokens=10000,
        messages = [
            {"role": "system", "content" : "You are a text analyser and can read the abstract text of research papers that have been clustered to gether based on text embedding similarity and you are able to extract what the texts are about, why were they clustered together. You provide this service as part of a tool for litterature review analysis where researchers see bunch of papers clustered together and they select a cluster and you tell them what that part of the umap embedding visualisation is about. This allows the researchers to detect topics in papers. " + extra_system_prompt},
            {"role": "user", "content": prompt}
        ],
        response_format = {
            "type": "json_schema",
            "json_schema": {
                "name": "extracted_data",
                "strict": True,
                "schema": {
                    "type": "object",
                    "properties": {
                        "headline": {
                            "type": "string",
                            "description": "Headline or name for this cluster",
                        },
                        "description": {
                            "type": "string",
                            "description": "A text describing what this cluster of abastracts is about",
                        },
                        "topics": {
                            "type": "array",
                            "items": {
                                "type": "string",
                                "description": "A key topic or keyword extracted from abstracts in this cluster",
                            }
                        },                        
                    },
                    "required": ["headline", "description", "topics"],
                    "additionalProperties": False
                }
            }
        },
        n=1,
        stop=None,
        temperature=0
    )
    # Extract the topic from the response
    topic_json = response.choices[0].message.content
    data = json.loads(topic_json)  # Convert JSON string to a dictionary
    return data;

    # Convert the filtered DataFrame to a list of titles

    #return NotStr("<br>".join(filtered_titles))



In [72]:
level_headlines = {}
cluster_info = {}

In [77]:
for i in range(1, 26):
    column = f"labels_{i}"
    # Get unique cluster labels in the current column
    unique_clusters = sorted(df[column].unique())
    cluster_amount = len(unique_clusters)

    print(f"{cluster_amount} clusters:")
    
    if i not in level_headlines:
        level_headlines[i] = [None] * cluster_amount
    
    if i not in cluster_info:
        cluster_info[i] = {}

    # Split the DataFrame into separate DataFrames for each cluster
    for cluster in range(0, cluster_amount):
        # Select only the 'title' column for each cluster and limit to first 5 entries
        titles = df[df[column] == cluster]['title'].head(5).tolist()
        
        # Truncate each title to a maximum of 30 characters
        truncated_titles = [title for title in titles]
        if cluster not in cluster_info[i]:
        # Call function X and store the result
            result = get_category_from_embeddings(truncated_titles, len(unique_clusters), cluster, level_headlines)
            cluster_info[i][cluster] = result
        else:
            result = cluster_info[i][cluster]

        level_headlines[i][cluster] = result["headline"]



1 clusters:
2 clusters:
3 clusters:
4 clusters:
5 clusters:
[[0.006785358767956495, 0.008609892800450325, 0.05299496650695801, 0.021536657586693764, 0.058337390422821045, 0.00927769672125578, 0.019330522045493126, -0.0009137577144429088, -0.04319256544113159, 0.017076686024665833, 0.029120994731783867, -0.030599702149629593, -0.01978367380797863, -0.004928031004965305, 0.01634925603866577, -0.0049041807651519775, -0.0031959160696715117, 0.003941232338547707, 0.052374862134456635, 0.004907161928713322, 0.04006820172071457, -0.0035238550044596195, 0.04266786202788353, 0.0294071976095438, -0.05704948678612709, -0.03343786671757698, -0.01755368709564209, 0.000778110115788877, 0.0005824646214023232, 0.012199335731565952, 0.03715848550200462, -0.029693398624658585, 0.028023889288306236, 0.025424227118492126, 0.020701903849840164, 0.04252476245164871, -0.05018065124750137, 0.04727093502879143, -0.03152985870838165, 0.0008645668276585639, 0.007846688851714134, -0.03436802327632904, 0.032650813

/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['embedding'] = filtered_df['embedding'].apply(ast.literal_eval)
/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['distance_to_centroid'] = cosine_distances(filtered_df['embedding'].tolist(), [centroid]).flatten()
2024-11-22 12:26:11,322 - INFO - HTTP Request: POST https://oai-saa

Function get_category_from_embeddings took 5.7992 seconds
[[-0.014081898145377636, 0.011310645379126072, 0.06239079311490059, 0.025525610893964767, 0.023593254387378693, 0.03313932195305824, 0.0013480206253007054, 0.01420917920768261, -0.03725859522819519, 0.03135738894343376, 0.004689144901931286, -0.04339122399687767, -0.01110236719250679, -0.05466137081384659, -0.00016036673332564533, 0.016014253720641136, 0.014151324518024921, -0.04133158549666405, 0.027770383283495903, 0.036749474704265594, 0.03397243469953537, -0.0020249236840754747, 0.01936984248459339, -0.011200721375644207, -0.0006291727186180651, -0.022413013502955437, 0.007764135953038931, -0.006560753099620342, 0.0027452181093394756, -0.01647709310054779, 0.030084582045674324, -0.026705851778388023, -0.0054672942496836185, 0.03700403496623039, 0.028973765671253204, 0.07673882693052292, -0.013364496640861034, 0.05012553930282593, -0.04517315700650215, 0.03200536593794823, 0.037628866732120514, -0.0010037836618721485, 0.02654

2024-11-22 12:26:16,400 - INFO - HTTP Request: POST https://oai-saari-swe.openai.azure.com//openai/deployments/gpt-4o/chat/completions?api-version=2024-10-21 "HTTP/1.1 200 OK"
/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['embedding'] = filtered_df['embedding'].apply(ast.literal_eval)
/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fil

Function get_category_from_embeddings took 5.0780 seconds
[[-0.005578392185270786, 0.011284582316875458, 0.014147263020277023, -0.015936437994241714, 0.007834031246602535, 0.0036007147282361984, 0.019617026671767235, 0.029572507366538048, -0.04314468055963516, 0.00858165044337511, -0.0237576887011528, -0.07074909657239914, -0.004977740813046694, -0.05362413451075554, -0.0006006516050547361, 0.01948922872543335, -0.008025728166103363, -0.01846684329211712, 0.026070836931467056, 0.003770047565922141, 0.05372637137770653, -0.02480563521385193, 0.010172738693654537, -0.028499003499746323, 0.006939443293958902, -0.02423054166138172, 0.03726596012711525, 0.012492275796830654, 0.008926705457270145, -0.025559643283486366, 0.016562649980187416, -0.043988145887851715, -0.04513832926750183, -0.0002508040051907301, -0.002770026447251439, 0.06880655884742737, 0.008006558753550053, 0.046646349132061005, -0.04580288007855415, 0.07228267192840576, 0.02273530326783657, -0.02178959548473358, -0.01456899

...

2024-11-22 12:39:16,521 - INFO - HTTP Request: POST https://oai-saari-swe.openai.azure.com//openai/deployments/gpt-4o/chat/completions?api-version=2024-10-21 "HTTP/1.1 200 OK"
/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['embedding'] = filtered_df['embedding'].apply(ast.literal_eval)
/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fil

Function get_category_from_embeddings took 44.8040 seconds
[[0.004559173248708248, 0.03901613503694534, 0.028927167877554893, -0.006681547034531832, 0.019877174869179726, 0.023185480386018753, -0.03398532047867775, 0.031770672649145126, -0.004651450552046299, 0.045933499932289124, 0.02829831652343273, -0.04809346795082092, -0.042379122227430344, -0.019576421007514, 0.04065661504864693, 0.025140387937426567, 0.030403602868318558, -0.04885902628302574, 0.012747913599014282, 0.04806612804532051, 0.03502429276704788, -0.0348329059779644, 0.018797190859913826, -0.008954298682510853, -0.008605696260929108, -0.03300103172659874, 0.018332388252019882, 0.012269439175724983, -0.004026016686111689, -0.02728668600320816, 0.045988183468580246, -0.034477464854717255, -0.010963888838887215, -0.027040613815188408, -0.028763120993971825, 0.03595390170812607, -0.016076724976301193, 0.055256906896829605, -0.07305613905191422, 0.015324837528169155, 0.011572234332561493, -0.03715692088007927, 0.00427892431

2024-11-22 12:39:24,143 - INFO - HTTP Request: POST https://oai-saari-swe.openai.azure.com//openai/deployments/gpt-4o/chat/completions?api-version=2024-10-21 "HTTP/1.1 200 OK"
/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['embedding'] = filtered_df['embedding'].apply(ast.literal_eval)
/var/folders/bf/4pk3n3917lv30ykyw5g_g0mw0000gn/T/ipykernel_85914/3626376620.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fil

Function get_category_from_embeddings took 7.6218 seconds
[[0.006785358767956495, 0.008609892800450325, 0.05299496650695801, 0.021536657586693764, 0.058337390422821045, 0.00927769672125578, 0.019330522045493126, -0.0009137577144429088, -0.04319256544113159, 0.017076686024665833, 0.029120994731783867, -0.030599702149629593, -0.01978367380797863, -0.004928031004965305, 0.01634925603866577, -0.0049041807651519775, -0.0031959160696715117, 0.003941232338547707, 0.052374862134456635, 0.004907161928713322, 0.04006820172071457, -0.0035238550044596195, 0.04266786202788353, 0.0294071976095438, -0.05704948678612709, -0.03343786671757698, -0.01755368709564209, 0.000778110115788877, 0.0005824646214023232, 0.012199335731565952, 0.03715848550200462, -0.029693398624658585, 0.028023889288306236, 0.025424227118492126, 0.020701903849840164, 0.04252476245164871, -0.05018065124750137, 0.04727093502879143, -0.03152985870838165, 0.0008645668276585639, 0.007846688851714134, -0.03436802327632904, 0.03265081346

KeyboardInterrupt: 

In [74]:
level_headlines

{1: ['Maritime Digital Twin Applications'],
 2: ['Digital Twin and Data Integration in Industry 4.0',
  'Maritime Digital Twin Innovations'],
 3: ['Maritime Digital Twin for Efficiency and Structural Evaluation',
  'Maritime Digital Twin Architectures and Applications',
  'Industrial Data Integration and Applications in Industry 4.0'],
 4: ['Maritime Digital Collaboration and Communication Technologies',
  'Maritime Digital Twin for Real-Time Operations and Data Management',
  'Industrial Data Integration and Applications in Smart Manufacturing',
  'Maritime Digital Twin for Operational Efficiency and Environmental Compliance']}

In [78]:
def print_level_headlines(level_headlines):
    for level, headlines in level_headlines.items():
        print(f"Level {level}:")
        for index, headline in enumerate(headlines, start=1):
            print(f"  {index}. {headline}")
        print()  # Add a blank line between levels for better readability
print_level_headlines(level_headlines)

Level 1:
  1. Maritime Digital Twin Applications

Level 2:
  1. Digital Twin and Data Integration in Industry 4.0
  2. Maritime Digital Twin Innovations

Level 3:
  1. Maritime Digital Twin for Efficiency and Structural Evaluation
  2. Maritime Digital Twin Architectures and Applications
  3. Industrial Data Integration and Applications in Industry 4.0

Level 4:
  1. Maritime Digital Collaboration and Communication Technologies
  2. Maritime Digital Twin for Real-Time Operations and Data Management
  3. Industrial Data Integration and Applications in Smart Manufacturing
  4. Maritime Digital Twin for Operational Efficiency and Environmental Compliance

Level 5:
  1. Maritime Digital Collaboration and Communication Technologies
  2. Maritime Digital Twin Architectures and Real-Time Applications
  3. Model-Driven Digital Twin Construction and Integration
  4. Maritime Digital Twin for Operational Efficiency and Environmental Compliance
  5. Industrial Information Integration and Monitori

In [95]:
from pydantic import BaseModel

class Cluster(BaseModel):
    label: str
    headline: str
    short_name: str
    description: str
    topics: list[str]

class Clusters(BaseModel):
    clusters: list[Cluster]

@timed
def get_category_from_embeddings_with_all_titles(all_titles, level_headlines=None):
    cluster_info = {}
   
    user_prompt = "Based on the following titles and abstracts (that are sorted by distance to the centroid of their text embeddings on text+abstract), what is the common topic?\n\n"
    
    system_prompt =  "You are a text analyser and can read the abstract text of research papers that have been clustered together based on text embedding similarity and you are able to extract what the texts are about, why were they clustered together. You provide this service as part of a tool for literature review analysis where researchers see a bunch of papers clustered together and they select a cluster and you tell them what that part of the UMAP embedding visualization is about. This allows the researchers to detect topics in papers. return a list of doctionaries, with the following attributes cluster_label, headline, short_name, description, topics" 

    for cluster_label, titles in all_titles.items():
        # Filter df for the current cluster using the titles
        cluster_df = df[df['title'].isin(titles)]

        # Ensure the embedding column is evaluated to a list
        cluster_df['embedding'] = cluster_df['embedding'].apply(ast.literal_eval)

        # Calculate the centroid of the embeddings for the current cluster
        centroid = np.mean(cluster_df['embedding'].tolist(), axis=0)
        
        # Calculate the cosine distance between each embedding and the centroid
        cluster_df['distance_to_centroid'] = cosine_distances(cluster_df['embedding'].tolist(), [centroid]).flatten()

        # Sort the DataFrame by distance to the centroid
        sorted_df = cluster_df.sort_values(by='distance_to_centroid')

        top_papers = sorted_df[['title', 'abstract']].head(10).to_dict(orient='records')

        user_prompt += f"\n Papers in Cluster with label '{cluster_label}':"
        user_prompt +=  "\n======================\n"
        for paper in top_papers:
            title = paper['title']
            abstract = paper['abstract']
            user_prompt += f"Title: {title}\nAbstract: {abstract}\n\n"


    # Prepare the prompt for OpenAI GPT-4
    extra_system_prompt = ""
    if level_headlines is not None:
        extra_system_prompt = f"""We are currently naming these clusters {level_headlines}.

        Make names specific, and bear in mind that the user will see the other clusters simultaneously 
        when this data is used, so avoid adding words that will be repeated in all clusters. And be to the point with headline and description, avoid text like 'this cluster is about...'"""



    # Call OpenAI GPT-4 to get the topic
    response = client.beta.chat.completions.parse(
        model="gpt-4o",
        max_tokens=10000,
        messages=[
            {"role": "system", "content": system_prompt + extra_system_prompt},
            {"role": "user", "content": user_prompt}
        ],
        response_format=Clusters,

        n=1,
        stop=None,
        temperature=0
    )
    # Extract the topic from the response
    topic_json = response.choices[0].message.content
    data = json.loads(topic_json)  # Convert JSON string to a dictionary
    cluster_info[cluster_label] = data

    return cluster_info

In [92]:
level_headlines2 = {}
cluster_info2 = {}

In [93]:
for i in range(1, 3):
    column = f"labels_{i}"
    # Get unique cluster labels in the current column
    unique_clusters = sorted(df[column].unique())
    cluster_amount = len(unique_clusters)

    print(f"{cluster_amount} clusters:")
    
    if i not in level_headlines2:
        level_headlines2[i] = [None] * cluster_amount
    
    if i not in cluster_info2:
        cluster_info2[i] = {}

    # Collect all titles for the current layer
    all_titles = {}
    for cluster in range(0, cluster_amount):
        titles = df[df[column] == cluster]['title'].tolist()
        all_titles[cluster] = titles

    # Call function once for the entire layer
    result = get_category_from_embeddings_with_all_titles(all_titles, level_headlines2)

    # Distribute results to each cluster
    for cluster in range(0, cluster_amount):
        if cluster not in cluster_info2[i]:
            cluster_info2[i][cluster] = result
        level_headlines2[i][cluster] = result["headline"]

1 clusters:


2024-11-22 13:39:29,383 - INFO - HTTP Request: POST https://oai-saari-swe.openai.azure.com//openai/deployments/gpt-4o/chat/completions?api-version=2024-10-21 "HTTP/1.1 200 OK"


Function get_category_from_embeddings_with_all_titles took 11.9897 seconds


KeyError: 'headline'

In [94]:
result

{0: {'steps': [{'label': '0',
    'headline': 'Digital Twin Applications in Maritime Industry',
    'short_name': 'Maritime Digital Twins',
    'description': 'This cluster focuses on the application of digital twin technology in the maritime industry, emphasizing efficiency, safety, and performance optimization. It covers topics such as fuel consumption estimation, structural health management, and autonomous ship navigation. The papers discuss integrating AI, IoT, and machine learning to enhance decision-making, predictive maintenance, and operational management in shipping.',
    'topivs': ['Digital Twin',
     'Maritime Industry',
     'AI and Machine Learning',
     'Predictive Maintenance',
     'Operational Efficiency']}],
  'final_answer': 'The common topic is the application of digital twin technology in the maritime industry, focusing on efficiency, safety, and performance optimization through AI, IoT, and machine learning.'}}